In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style('darkgrid')

import torch
import torch.nn as nn
dev = 'cuda:0' if torch.cuda.is_available() else 'cpu'

import ast
from termcolor import colored
from tqdm import tqdm
from utils import spacy_tokenizer
import spacy
from nltk.tokenize import TweetTokenizer 
tokenizer = TweetTokenizer()

# Gráficas en LaTeX, a veces da problemas, en ese caso comentar y reiniciar kernel
plt.rc('text', usetex=True)
plt.rc('font', family='serif')

# For my jupyter theme
%config InlineBackend.print_figure_kwargs = {'facecolor':'white'}

## Resultados

De los distintos preprocesamientos el que mayor F1 score tiene en `test` es poner los posts con [ ] como completamente tóxicos (**best-model-try2.pt**, *train*=0.6498 , *test*=0.6526), así que usaremos ese.

In [12]:
from utils import get_vocab, get_index_toxic_words, color_toxic_words, f1
import gdown

In [3]:
train = pd.read_csv('../Datos/tsd_train.csv', converters={'spans':ast.literal_eval})
test = pd.read_csv('../Datos/tsd_trial.csv', converters={'spans':ast.literal_eval})

In [4]:
# Nuestros embeddings
vocab = get_vocab()

/home/david/Documentos/PyTorch-1.x/lib/python3.7/site-packages/torchtext/data/field.py:150: UserWarning: Field class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)


In [5]:
class LSTMTagger(nn.Module):

    def __init__(self, embedding_dim, stacked_layers, dropout_p, weight, hidden_dim, vocab_size):
        super(LSTMTagger, self).__init__()
        self.hidden_dim = hidden_dim         # Dimension del estado oculta en cada direccion de la LSTM
        self.stacked_layers = stacked_layers # Cuantas capas en la LSTM
        
        self.word_embeddings = nn.Embedding.from_pretrained(weight)
        self.lstm = nn.LSTM(embedding_dim,
                            hidden_dim,
                            num_layers = stacked_layers,
                            dropout = dropout_p,
                            bidirectional = True)

        # Linear layers
        self.fc1 = nn.Linear(hidden_dim*2, 1) # 2 veces el tamaño de hidden_dim por ser bidireccional

    def forward(self, sentence):
        embeds = self.word_embeddings(sentence)
        output, _ = self.lstm(embeds.view(len(sentence), 1, -1))
        x = torch.sigmoid(self.fc1(output.view(len(sentence), -1)))
        return x

In [6]:
def prepare_sequence(seq):
    idxs = vocab.lookup_indices(seq)      # Si no está lo pone como 0
    return torch.tensor(idxs, dtype=torch.long, device=dev)

def prepare_sequence_tags(seq):
    tag_to_ix = {"non_toxic": 0, "toxic": 1} 
    idxs = [tag_to_ix[s] for s in seq]
    return torch.tensor(idxs, dtype=torch.long, device=dev)

def tagger_LSTM(text, threshold=0.5):
    """
    Hace el tagging con el modelo que entrenamos.
    """
    ix_to_tag = {0: 'non_toxic', 1: 'toxic'}
    words = spacy_tokenizer(text.lower()) # Parece funcionar mejor
    
    with torch.no_grad():
        inputs = prepare_sequence(words)
        tag_scores = model(inputs)
        
        tags = [1 if x > threshold else 0 for x in tag_scores]

        tagged_sentence = list(zip(words, tags))

    return tagged_sentence

El archivo con el modelo está algo pesado para GitHub, así que lo pondremos en un Drive para descargarlo.

In [14]:
url = 'https://drive.google.com/uc?id=1KO-QXUBfwzjauWLhiVi9StD3y0GtiBbj'
output = 'model.pt'

gdown.download(url, output, quiet=False) 

Downloading...
From: https://drive.google.com/uc?id=1KO-QXUBfwzjauWLhiVi9StD3y0GtiBbj
To: /home/david/Documentos/PyTorch-1.x/PLN/Proyecto_PLN/Notebooks/test.pt
204MB [02:02, 1.67MB/s] 


'test.pt'

In [15]:
model = torch.load('model.pt')
model.to(torch.device(dev))

LSTMTagger(
  (word_embeddings): Embedding(19611, 200)
  (lstm): LSTM(200, 600, num_layers=6, dropout=0.2, bidirectional=True)
  (fc1): Linear(in_features=1200, out_features=1, bias=True)
)

In [18]:
indices_test = []
for i,(gold_index,text) in enumerate(zip(test['spans'],test['text'])):
    tagged_sentence = tagger_LSTM(text)   
    prediction_index = get_index_toxic_words(text.lower(), tagged_sentence)
    indices_test.append(prediction_index)
    print(str(i) + colored(' Pred: ', color='cyan', attrs=['bold']) + 
           color_toxic_words(prediction_index, text))
    print(str(i) + colored(' Gold: ', color='yellow', attrs=['bold']) + 
          color_toxic_words(gold_index, text) + '\n'*2)

0 Pred: Because he's a moron and a bigot. It's not any more complicated than that.
0 Gold: Because he's a moron and a bigot. It's not any more complicated than that.


1 Pred: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.
1 Gold: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.


2 Pred: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...
2 Gold: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...


3 Pred: Trump Claimed that Russia will never invade the Ukraine, when Russia already has - how stupid can people be?
3 Gold: Trump Claim

6 Pred: Thanks a lot douchebag. You're the reason the Portland buttfuckers are getting pushed out and moving down south to the Wilsonville area and beyond. Because of you all the stupid fucking assholes that made Portland a place full of stupid fucking assholes are going to try to turn Salem into some kind of new-stupid-fucking-asshole-topia. This will drive up the price of housing and displace  people down here. Having lived in San Clemente for a time myself I think you're dumb as shit to have moved up here. The fucks wrong with you outsider. I hope bums shit in your yard everyday and never let you walk by without demanding spare  change.
6 Gold: Thanks a lot douchebag. You're the reason the Portland buttfuckers are getting pushed out and moving down south to the Wilsonville area and beyond. Because of you all the stupid fucking assholes that made Portland a place full of stupid fucking assholes are going to try to turn Salem into some kind of new-stupid-fucking-asshole-topia. This wi

9 Pred: You're wrong.  The delay between retirement and lobbying is nowhere near 7 years.  This law is specifically aimed at the SECDEF job.  The purpose of this separation is to ensure firm CIVILIAN leadership of the military.  Read the article.

You have no idea where I've worked.  Don't make ignorant statements.
9 Gold: You're wrong.  The delay between retirement and lobbying is nowhere near 7 years.  This law is specifically aimed at the SECDEF job.  The purpose of this separation is to ensure firm CIVILIAN leadership of the military.  Read the article.

You have no idea where I've worked.  Don't make ignorant statements.


10 Pred: Billy, are you a complete idiot, being thick headed or just not reading what people have been trying to tell you in response to your soapbox blathering.  A) Poor people without insurance need health care too. B) Planned Parenthood provides women's health care for free to anyone.  PP does these thru donations and grants from the States and Fed and Charit

13 Pred: Clinton should be the last person to say anything about anyone. She is such a lying scum bag. I can't handle just hearing her voice. It would be a lot worse if she was President than we are with the crazy Trump. She would have her husband (AKA: as the cigar rapist) as her guide. He should have been arrested for doing that to that young girl, the starred eye Monica. How can anyone blame her but I certainly wouldn't have let him stick a cigar in me. It is the Media's fault because they keep going to get her big lying mouth going.
13 Gold: Clinton should be the last person to say anything about anyone. She is such a lying scum bag. I can't handle just hearing her voice. It would be a lot worse if she was President than we are with the crazy Trump. She would have her husband (AKA: as the cigar rapist) as her guide. He should have been arrested for doing that to that young girl, the starred eye Monica. How can anyone blame her but I certainly wouldn't have let him stick a cigar in 

18 Pred: Ride those trailer brakes, you morons!
18 Gold: Ride those trailer brakes, you morons!


19 Pred: Of course you cannot defend your own hypocrisy...I see you are starting of 2017 on the same losing track as always...oh, well, no cure for stupidity.
19 Gold: Of course you cannot defend your own hypocrisy...I see you are starting of 2017 on the same losing track as always...oh, well, no cure for stupidity.


20 Pred: another comment proving yet again how completely brain washed stupid the likes of you have become
20 Gold: another comment proving yet again how completely brain washed stupid the likes of you have become


21 Pred: It didn't take much rope for the village idiot to hang himself.
21 Gold: It didn't take much rope for the village idiot to hang himself.


22 Pred: Clinton signed that Joint Fundraising agreement in August 2015. It was reported on then; why is it an issue now? And there wasn't anything illegal about it, so it's not a crime. Oh, and the Sanders campaign si

...

660 Pred: The Denver Donkeys are back!  The special teams coach, McCoy and the head coach should lose their jobs.  You put a guard in a tackle and can't figure out how to give the guy some help?  We never seem to do this.  Defense was good but still can't cover backs or TE's.  Special teams was less than special.  Offense with the great pretender at QB is terrible.  He must be the best practice player in the world but the worst when it comes to game time.  McNown was pretty bad too.  Run the freaking ball!  SD had the worst D against the run.  Denver is just being stupid.
660 Gold: The Denver Donkeys are back!  The special teams coach, McCoy and the head coach should lose their jobs.  You put a guard in a tackle and can't figure out how to give the guy some help?  We never seem to do this.  Defense was good but still can't cover backs or TE's.  Special teams was less than special.  Offense with the great pretender at QB is terrible.  He must be the best practice player in the world but

666 Pred: Because Trudeau knows that his federal Liberal Party survives on voters with brain damage from recreational pot use.
666 Gold: Because Trudeau knows that his federal Liberal Party survives on voters with brain damage from recreational pot use.


667 Pred: can she just kill herself already?............
667 Gold: can she just kill herself already?............


668 Pred: I will fight the White Nationalists along side you. Again, the assumptions.
668 Gold: I will fight the White Nationalists along side you. Again, the assumptions.


669 Pred: One can only hope they are this stupid !!! Lol
But - the democrats reaction and conduct to Trump being elected clearly demonstrates they are just plain Hippocrates and encourage violence to support their agenda!
669 Gold: One can only hope they are this stupid !!! Lol
But - the democrats reaction and conduct to Trump being elected clearly demonstrates they are just plain Hippocrates and encourage violence to support their agenda!


670 Pred

673 Pred: "Trump’s tax returns: What did we learn?"

----------

That Rachel Maddow is an idiot.

This entire episode has blown up in her face.

She deserves it.
673 Gold: "Trump’s tax returns: What did we learn?"

----------

That Rachel Maddow is an idiot.

This entire episode has blown up in her face.

She deserves it.


674 Pred: And do you define "solid proof'? Outside of mathematics and physics (correct me if there are others) you can never have definitive 'proof' of anything.

You can have evidence and in this case there seems to be many converging threads of evidence. The question is, why is all this evidence appearing in the political discourse now? Some people think that it's because Obama's a sore loser, or the intelligence communities want to embarass Trump, or they are simply inept. 

My theory is simpler. There is evidence because the attempt to influence the election was real and the dividends the Russians will accrue as a result are considerable. They aren't stupid.
674

677 Pred: Thank you Secretary Mnuchin!
Do not let the hypocrites win.
677 Gold: Thank you Secretary Mnuchin!
Do not let the hypocrites win.


678 Pred: You're a fake, alright...
678 Gold: You're a fake, alright...


679 Pred: Grand standing egomaniacs?   Oh I get it, unlike Trump and Clinton right?   The Dems and the Reps are two sides of the same corrupt coin, if you want the same old crap feel free to vote for the same old crap.
679 Gold: Grand standing egomaniacs?   Oh I get it, unlike Trump and Clinton right?   The Dems and the Reps are two sides of the same corrupt coin, if you want the same old crap feel free to vote for the same old crap.


680 Pred: Are you a Woman? No? Then why are you commenting and making light of a Woman's issue? Can't even shut your mouth and posts more than once! WHY? Was your pu**y grabbed? Were you talked about as chattel? Were you insulted over and over again? No? Then why are you even on this thread? You are so freaking ignorant that YOU epitomize Tru

684 Pred: this governors a moron. Alaska is its own worst enemy on this was just a statement of fact not an insult maybe walker should listen to the customer and find out what they want.
684 Gold: this governors a moron. Alaska is its own worst enemy on this was just a statement of fact not an insult maybe walker should listen to the customer and find out what they want.


685 Pred: But ... Trump's not bluffing. He's prepared to go scorched earth. As President he has that economic  power.  And yes, he is that stupid.  

So now what's your "Plan B"?
685 Gold: But ... Trump's not bluffing. He's prepared to go scorched earth. As President he has that economic  power.  And yes, he is that stupid.  

So now what's your "Plan B"?


686 Pred: Can't believe the limited knowledge of this Article and the Comments.   Unbelievable, not even going to attempt to argue with stupid.
686 Gold: Can't believe the limited knowledge of this Article and the Comments.   Unbelievable, not even going to attemp

In [19]:
score_test = [f1(pred, gold) for pred,gold in zip(indices_test, test['spans'])]
print('F1 in test: {:.6f}'.format(np.mean(score_test)))

F1 in test: 0.651567


## Predicción en el dataset de *evaluation*

In [ ]:
evaluation = pd.read_csv('../Datos/tsd_test.csv')

In [23]:
indices_evaluation = []
for i,text in enumerate(evaluation['text']):
    tagged_sentence = tagger_LSTM(text)   
    prediction_index = get_index_toxic_words(text.lower(), tagged_sentence)
    indices_evaluation.append(prediction_index)
    print(str(i) + colored(' Pred: ', color='cyan', attrs=['bold']) + 
           color_toxic_words(prediction_index, text) + '\n') 

  0%|          | 3/2000 [00:00<01:16, 25.95it/s]

0 Pred: That's right. They are not normal. And I am starting from the premise that they are ABNORMAL. Proceed wth the typical racist, bigot, sexist rubbish.
Thanks!

1 Pred: "Watch people die from taking away their healthcare"

DING DING DING!  Winner of stupid post of the day award!

2 Pred: tens years ago i contacted the PDR and suggested that the time might be good to work with alaska on building a gas line.. alaska rejected them without even consideration despite china being flush with cash and hungry for gas.. and set up another infamous boondoggle.. the transcanada-exxon rip off that we are still paying for and have yet to receive anything of value.. hundreds of millions of dollars on studies.. and buyouts.. i hope china says f you alaska.. you are nothing but ignorant people..

3 Pred: The parallels between the ANC and the Sicilian Mafia are glaring. The ANC has always been run by a few "families" who treat the state as 'turf' ; as just one big piggy bank for their self-enrichme

  1%|          | 11/2000 [00:00<01:01, 32.41it/s]

4 Pred: Intel Community: ‘How can we work for a President who Undermines our work?’

Days before taking office, he compared America’s spies to Adolf Hitler’s Gestapo.

American spies do not like having their work dismissed by the president. Nor do they appreciate comparisons to Nazi Germany.

Former CIA Director John Brennan made it clear: “The person who said that should be ashamed of himself,” Brennan said.

Coats’ predecessor, Gen. James Clapper, called Trump’s comments “a terrible, insulting affront … completely inappropriate.”

Trump’s opinions are out of step with the conclusions of the agencies he is supposed to be leading.

Not surprising in a treasonous traitor.

5 Pred: I live in an area that saw major flood damage in 2013, including areas that were very unexpected. Trump's reversal is just plain stupid.

6 Pred: Elaine Marie Jeffers sounds like a sociopath 😕.

7 Pred: A rock has more mental horsepower than the indubitably ignorant. And more integrity as well. They're largely

  1%|          | 22/2000 [00:00<00:46, 42.31it/s]

...

1977 Pred: I believe  there are more felons out there that have more weapons than the good people in society have...........

The SOLUTION:  Build more jails and keep these IDIOTS out of society, FOREVER...................

1978 Pred: WOW!! Can't believe it is still that high. The contempt these Provincial Liberals have towards the private citizens footing the bill for their money squandering ways is absolutely disgusting! When the province is being dismantled and ran into the ground there is no better example then recent quote from Liz Sandals about Go Train riders as well as idiot Glen Thibeault telling families  deciding between paying hydro or food and small businesses pleading for relief to go spend $10 to $30, 000 upgrading homes and businesses to higher efficiency lighting and equipment. ABSOLUTELY SICKENING AND DISPACABLE PEOPLE!! They are pretty much everything I am trying to raise my kids not to be.

1979 Pred: The "human rights" squad need a swift kick in the derriere.

1980

100%|█████████▉| 1990/2000 [00:52<00:00, 39.04it/s]

1983 Pred: That's OK - Liberal's double down on the stupid by bringing them to Canada instead.

1984 Pred: Blah, Blah, Blah. The Obama administration sucked, end of story.

1985 Pred: Keep hiring imbeciles like this jerk and you will end up with a no firearms for rent-a-cops bill next session.

1986 Pred: Asshole.

1987 Pred: Calling tens of millions of voters "deplorable" or "stupid" (because they voted for the other guy) is condescending. 

But hey, feel free.  It's working so well for you guys.

1988 Pred: "molesting his own daughter and betraying America to Russia"
The first part of that sentence makes you a disgusting liar. The second part makes you galactically stupid.

1989 Pred: And that would have been the best course of action. Pit bull owners pull this crap all the time.

1990 Pred: There ya go. Stupidity to the max.

1991 Pred: Sanders has balls unlike Treyson Goowdy.The Gowdy is a blow hard, has done nothing.What a loser

1992 Pred: It's really hard to say this since there

100%|██████████| 2000/2000 [00:53<00:00, 37.60it/s]

1995 Pred: hey loser change your name to something more accurate, as in alt left ignorant for life!,, unlike the dems who take their money from soros or wall street as well,, save it loser you lose again. this is about fixing the mess obamacare created

1996 Pred: And you are a complete moron who obviously doesn't know the meaning of the word narcissist. By the way your bias is showing.

1997 Pred: Such vitriol from the left.  Who would have thought these open minded, tolerant people could be so vile and hateful? It so exposes you all for what you are, hypocrites.

1998 Pred: It is now time for most of you to expand your pebble minds.

1999 Pred: Why does this author think she can demand, or is owed anything from either of these two people? One guy is a goon, the other is illiterate. They aren't law makers, teachers, or in any kind moral authority position. They are entertainers who get punched for her pleasure, and will likely live out their days mentally debilitated from the repeated

In [24]:
evaluation['spans'] = indices_evaluation
evaluation = evaluation[['spans', 'text']]
evaluation.head()

spans  \
0  [102, 103, 104, 118, 119, 120, 121, 122, 123, ...   
1                           [81, 82, 83, 84, 85, 86]   
2           [483, 484, 485, 486, 487, 488, 489, 490]   
3           [413, 414, 415, 416, 417, 418, 419, 420]   
4  [150, 151, 152, 153, 154, 155, 156, 473, 474, ...   

                                                text  
0  That's right. They are not normal. And I am st...  
1  "Watch people die from taking away their healt...  
2  tens years ago i contacted the PDR and suggest...  
3  The parallels between the ANC and the Sicilian...  
4  Intel Community: ‘How can we work for a Presid...

Para la evaluación se debe subir un zip con un archivo txt de la siguiente manera (al final subir el archivo `spans-pred.zip` que se produce):

In [27]:
predictions = evaluation['spans'].tolist()
ids = evaluation.index.tolist()

with open("spans-pred.txt", "w") as out:
    for uid, text_scores in zip(ids, predictions):
        out.write(f"{str(uid)}\t{str(text_scores)}\n")
        
# Zip the predictions
! zip -r spans-pred.zip ./spans-pred.* 
! rm spans-pred.txt
! mv spans-pred.zip ../spans-pred.zip

updating: spans-pred.txt (deflated 84%)
